In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
!pip install pythainlp

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.9/17.9 MB 35.6 MB/s eta 0:00:00


In [4]:
import pandas as pd
import numpy as np
from pythainlp import word_tokenize
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline
from sklearn.metrics import classification_report, confusion_matrix
# import joblib
# import seaborn as sns
import matplotlib.pyplot as plt
from imblearn.over_sampling import SMOTE
import json
import glob

from pythainlp.corpus import thai_stopwords

In [5]:
file_pattern = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/TripAdvisor_reviews_EN.csv')

In [6]:
file_pattern

Unnamed: 0  helpful_votes  location_id lang  review_id  \
0              0              0      2209612   en  953596359   
1              1              0      2209612   en  938998692   
2              2              6      2209612   en  933065689   
3              3              0      2209612   en  885904967   
4              4              4      2209612   en  782967555   
...          ...            ...          ...  ...        ...   
5904        5904              0      1831068   en  888281929   
5905        5905              4      1831068   en  752115552   
5906        5906              0      1831068   en  693354319   
5907        5907              1      1831068   en  573376614   
5908        5908              0      1831068   en  571939282   

                                                 review  \
0     Besides elegant grand palace and wat pra kaew ...   
1     This is one of the last big king temples of Ba...   
2     It is beautiful, clean and free to enter. Both...   
3     Wat Ratchabophit is a Buddhist temple located ...   
4     Wat Ratchabophit is a historic royal temple bu...   
...                                                 ...   
5904  Is quite far from Korat Town or main highway. ...   
5905  Prasat Pueai Noi is claimed to be the biggest ...   
5906  I think this place is claimed to be the oldest...   
5907  The compound comprises three brick buildings o...   
5908  Fully recommend this to the genuine history bu...   

                                         review_subject        trip_type  \
0     The place is nearby grand palace, in the area ...           Family   
1                                              Nice Wat      Solo travel   
2                                            Nice views      Solo travel   
3     Wat Ratchabophit - a temple characterized by u...          Couples   
4                                   Beautiful, peaceful             NONE   
...                                                 ...              ...   
5904                 Can visit.. depends on individual            Family   
5905                    Small, Isolated Khmer Sanctuary             NONE   
5906                         A sense of ancient times..  Friends getaway   
5907                                 Another Angkor Wat      Solo travel   
5908                          Small, simple, yet qualit          Couples   

     travel_date  rating     location_name    province   place_id  
0     2024-05-31       5  Wat Ratchabophit     Bangkok  P03013220  
1     2024-02-29       4  Wat Ratchabophit     Bangkok  P03013220  
2     2023-12-31       4  Wat Ratchabophit     Bangkok  P03013220  
3     2022-10-31       5  Wat Ratchabophit     Bangkok  P03013220  
4     2021-01-31       5  Wat Ratchabophit     Bangkok  P03013220  
...          ...     ...               ...         ...        ...  
5904  2023-04-30       3   Prasat Puay Noi  Nonthaburi  P03013503  
5905  2019-09-30       3   Prasat Puay Noi  Nonthaburi  P03013503  
5906  2019-06-30       4   Prasat Puay Noi  Nonthaburi  P03013503  
5907  2018-04-30       4   Prasat Puay Noi  Nonthaburi  P03013503  
5908  2018-04-30       4   Prasat Puay Noi  Nonthaburi  P03013503  

[5909 rows x 13 columns]

In [ ]:
file_pattern = 'dataset/TripAdvisor_reviews_EN_Set-*.json'
files = glob.glob(file_pattern)

# Step 2: Initialize an empty list to store the combined data
combined_reviews_data = []

# Step 3: Load each file and concatenate the contents
for file in files:
    with open(file, 'r') as f:
        data = json.load(f)
        combined_reviews_data.extend(data)

In [ ]:
combined_reviews_data

[{'2209612': [{'id': 953596359,
    'lang': 'en',
    'location_id': 2209612,
    'published_date': '2024-06-03T12:40:41Z',
    'rating': 5,
    'helpful_votes': 0,
    'rating_image_url': 'https://www.tripadvisor.com/img/cdsi/img2/ratings/traveler/s5.0-66827-5.svg',
    'url': 'https://www.tripadvisor.com/ShowUserReviews-g293916-d2209612-r953596359-Reviews-Wat_Ratchabophit-Bangkok.html?m=66827#review953596359',
    'text': 'Besides elegant grand palace and wat pra kaew (emerald Buddha temple), this is another temple of a must visit, this temple is made of porcelain.',
    'title': 'The place is nearby grand palace, in the area of old Bangkok city, easy to find and a must visit place of temples in old',
    'trip_type': 'Family',
    'travel_date': '2024-05-31',
    'user': {'username': '868phenp',
     'user_location': {'id': '293916', 'name': 'Bangkok'},
     'avatar': {'thumbnail': 'https://media-cdn.tripadvisor.com/media/photo-t/1a/f6/e7/7b/default-avatar-2020-56.jpg',
      'small

In [ ]:
len(combined_reviews_data)

1427

In [ ]:
tripadvisor_central_attraction_locations = pd.read_csv("dataset/TripAdvisor_Location_Ids.csv")
tripadvisor_central_attraction_locations

Unnamed: 0  location_id  \
0              0      2209612   
1              1      2273363   
2              2       311043   
3              3       317504   
4              4       456322   
...          ...          ...   
1899        6905     13009981   
1900        6906      3256228   
1901        6907      2515972   
1902        6911     13365103   
1903        6912      2645868   

                                                 name         province  \
0                                    Wat Ratchabophit          Bangkok   
1     Wat Rajapradit Sathitmahasimaram Rajaworavihara          Bangkok   
2                                  Wat Phra Chetuphon          Bangkok   
3                           Temple Of Dawn (Wat Arun)          Bangkok   
4                                           Wat Umong          Bangkok   
...                                               ...              ...   
1899                               Thai Sabai Massage  Samut Songkhram   
1900                          Phuket Dragon Muay Thai  Samut Songkhram   
1901                       Thai Cooking School Phuket  Samut Songkhram   
1902                     Nong Bua Thai Dessert Market  Samut Songkhram   
1903                     Free Thai (Seri Thai) Museum  Samut Songkhram   

       place_id  
0     P03013220  
1     P03013220  
2     P03013220  
3     P03013220  
4     P03013220  
...         ...  
1899  P03012297  
1900  P03012297  
1901  P03012297  
1902  P03000251  
1903  P03000251  

[1904 rows x 5 columns]

In [ ]:
normalize_reviews_data = pd.DataFrame()

for location_data in combined_reviews_data:
    for location_id, reviews in location_data.items():
        print(f"Location ID: {location_id}")

        # Iterate over each review in the list of reviews
        for review in reviews:
            # Create a DataFrame for each review
            review_df = pd.DataFrame([{
                "helpful_votes": review.get("helpful_votes", 0),
                "location_id": review.get("location_id", None),
                "lang": review.get("lang", None),
                "review_id": review.get("id", None),
                "review": review.get("text", None),
                "review_subject": review.get("title", None),
                "trip_type": review.get("trip_type", None),
                "travel_date": review.get("travel_date", None),
                "rating": review.get("rating", 0)
            }])

            # Concatenate the current review DataFrame with the normalized DataFrame
            normalize_reviews_data = pd.concat([normalize_reviews_data, review_df], ignore_index=True)

normalize_reviews_data.replace("None", None, inplace=True)

Location ID: 2209612
Location ID: 2273363
Location ID: 311043
Location ID: 317504
Location ID: 456322
Location ID: 1368436
Location ID: 7913913
Location ID: 447648
Location ID: 456623
Location ID: 1235228
Location ID: 2405697
Location ID: 456261
Location ID: 496987
Location ID: 8595513
Location ID: 456262
Location ID: 2274256
Location ID: 311044
Location ID: 7660023
Location ID: 13347726
Location ID: 12378803
Location ID: 552410
Location ID: 9706798
Location ID: 17131275
Location ID: 2723894
Location ID: 4322574
Location ID: 1229768
Location ID: 3750296
Location ID: 6420124
Location ID: 4322691
Location ID: 6621070
Location ID: 2721120
Location ID: 6487057
Location ID: 6669467
Location ID: 8514333
Location ID: 8595657
Location ID: 8595612
Location ID: 12879873
Location ID: 9582501
Location ID: 14141392
Location ID: 17130682
Location ID: 549695
Location ID: 13197945
Location ID: 10842868
Location ID: 456320
Location ID: 4773504
Location ID: 4322927
Location ID: 2724111
Location ID: 4322

In [ ]:
normalize_reviews_data

helpful_votes  location_id lang  review_id  \
0                 0      2209612   en  953596359   
1                 0      2209612   en  938998692   
2                 6      2209612   en  933065689   
3                 0      2209612   en  885904967   
4                 4      2209612   en  782967555   
...             ...          ...  ...        ...   
5904              0      1831068   en  888281929   
5905              4      1831068   en  752115552   
5906              0      1831068   en  693354319   
5907              1      1831068   en  573376614   
5908              0      1831068   en  571939282   

                                                 review  \
0     Besides elegant grand palace and wat pra kaew ...   
1     This is one of the last big king temples of Ba...   
2     It is beautiful, clean and free to enter. Both...   
3     Wat Ratchabophit is a Buddhist temple located ...   
4     Wat Ratchabophit is a historic royal temple bu...   
...                                                 ...   
5904  Is quite far from Korat Town or main highway. ...   
5905  Prasat Pueai Noi is claimed to be the biggest ...   
5906  I think this place is claimed to be the oldest...   
5907  The compound comprises three brick buildings o...   
5908  Fully recommend this to the genuine history bu...   

                                         review_subject        trip_type  \
0     The place is nearby grand palace, in the area ...           Family   
1                                              Nice Wat      Solo travel   
2                                            Nice views      Solo travel   
3     Wat Ratchabophit - a temple characterized by u...          Couples   
4                                   Beautiful, peaceful             NONE   
...                                                 ...              ...   
5904                 Can visit.. depends on individual            Family   
5905                    Small, Isolated Khmer Sanctuary             NONE   
5906                         A sense of ancient times..  Friends getaway   
5907                                 Another Angkor Wat      Solo travel   
5908                          Small, simple, yet qualit          Couples   

     travel_date  rating  
0     2024-05-31       5  
1     2024-02-29       4  
2     2023-12-31       4  
3     2022-10-31       5  
4     2021-01-31       5  
...          ...     ...  
5904  2023-04-30       3  
5905  2019-09-30       3  
5906  2019-06-30       4  
5907  2018-04-30       4  
5908  2018-04-30       4  

[5909 rows x 9 columns]

In [ ]:
merged_df = normalize_reviews_data.merge(tripadvisor_central_attraction_locations[['location_id', 'name', 'province', 'place_id']], on='location_id', how='left')

# Rename the 'name' column to 'location_name'
merged_df.rename(columns={'name': 'location_name'}, inplace=True)
len(merged_df)

5909

In [ ]:
# merged_df.to_csv("dataset/TripAdvisor_reviews_EN.csv")
EN_tripadvisor_reviews = pd.read_csv("dataset/TripAdvisor_reviews_EN.csv")

In [ ]:
# Define Thai stop words
thai_stopwords = thai_stopwords()

# Function to normalize text
def normalize_text(text):
    tokens = word_tokenize(text, engine='newmm')
    tokens = [token for token in tokens if token not in thai_stopwords and token.isalpha()]
    return ' '.join(tokens)

In [ ]:
thai_stopwords

frozenset({'กลุ่มก้อน',
           'จาก',
           'ครั้งก่อน',
           'พวกฉัน',
           'กันเอง',
           'เพียงเพราะ',
           'อันที่',
           'ทุกเมื่อ',
           'เสมือนว่า',
           'ช้า',
           'ยิ่ง',
           'เชื่อ',
           'คราวก่อน',
           'เช่นก่อน',
           'แต่ก็',
           'ทั้งมวล',
           'คราวใด',
           'ครัน',
           'เมื่อคืน',
           'ดั่งเก่า',
           'จวบจน',
           'ไป่',
           'รวมทั้ง',
           'เรื่อยๆ',
           'จัดแจง',
           'ช่วงต่อไป',
           'แรก',
           'มุ่งหมาย',
           'นับแต่นั้น',
           'เพียงเพื่อ',
           'ค่อนข้างจะ',
           'ด้วยเหมือนกัน',
           'สมัยก่อน',
           'ใหญ่โต',
           'ถึงแม้จะ',
           'รวมด้วย',
           'เพียงแค่',
           'ภายนอก',
           'จู่ๆ',
           'พวกนี้',
           'นอก',
           'บ่อย',
           'เท่าที่',
           'คราวๆ',
           'แต่ไร',
           'ภายภาค',
    

In [ ]:
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer
from nltk.stem import WordNetLemmatizer
import string

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')


In [ ]:
def preprocess_text(text):
    # Lowercasing
    text = text.lower()

    # Removing punctuation
    text = text.translate(str.maketrans('', '', string.punctuation))

    # Tokenization
    tokens = word_tokenize(text)

    # Removing stopwords
    stop_words = set(stopwords.words('english'))
    tokens = [word for word in tokens if word not in stop_words]

    # Stemming (optional)
    stemmer = PorterStemmer()
    tokens = [stemmer.stem(word) for word in tokens]

    # Lemmatization (optional)
    lemmatizer = WordNetLemmatizer()
    tokens = [lemmatizer.lemmatize(word) for word in tokens]

    # Return the preprocessed text as a string of tokens
    return ' '.join(tokens)
